In [1]:
import psycopg2
import pandas as pd
import psycopg2.extras as extras
import os
from os import listdir
from os.path import isfile, join

In [25]:
os.chdir("C:/Users/pauli/Documents/M2/Text Mining/projet/Disney-Text-Mining/fichiers/tables")
mypath = os.getcwd()


client = pd.read_csv(str(mypath)+"/client.csv",sep=';')
date = pd.read_csv(str(mypath)+"/date.csv",sep=';')
hotel = pd.read_csv(str(mypath)+"/hotel.csv",sep=';')
room = pd.read_csv(str(mypath)+"/room.csv",sep=';')
reservation = pd.read_csv(str(mypath)+"/reservation.csv",sep=';')

# Oracle

In [26]:
#??
#compass club 
#empire state club 

# MySQL

In [27]:
#??

# PostgreSQL

In [28]:
#https://waytolearnx.com/2020/06/connexion-a-une-base-de-donnees-postgresql-en-python.html

In [29]:
conn = psycopg2.connect(
          user = "m139",
          password = "m139",
          host = "db-etu.univ-lyon2.fr",
          port = "5432",
          database = "m139"
    )

In [10]:
conn = psycopg2.connect(
          user = "m140",
          password = "m140",
          host = "db-etu.univ-lyon2.fr",
          port = "5432",
          database = "m140"
    )

# execute request 

In [30]:
def execute_req(conn, req):
    try: 
        cursor = conn.cursor()
        cursor.execute(req)
        conn.commit()
        cursor.close()
    except (Exception, psycopg2.Error) as error :
        print ("Erreur lors de la création du table PostgreSQL", error)

# drop

In [31]:
sql_drop_reservation = '''DROP TABLE reservation; '''
execute_req(conn, sql_drop_reservation)

In [32]:
sql_drop_date = '''DROP TABLE date; '''
execute_req(conn, sql_drop_date)

In [33]:
sql_drop_client = '''DROP TABLE client; '''
execute_req(conn, sql_drop_client)

In [34]:
sql_drop_room = '''DROP TABLE room; '''
execute_req(conn, sql_drop_room)

In [35]:
sql_drop_hotel = '''DROP TABLE hotel; '''
execute_req(conn, sql_drop_hotel)

## create tables

In [36]:
sql_create_hotel = '''CREATE TABLE HOTEL(
    id_hotel TEXT PRIMARY KEY NOT NULL,
    hotel VARCHAR(100),
    level_hotel INT
  ); '''

execute_req(conn, sql_create_hotel)

In [37]:
sql_create_room = '''CREATE TABLE ROOM(
    id_room TEXT PRIMARY KEY NOT NULL,
    room_type TEXT,
    id_hotel TEXT,
    CONSTRAINT ROOM_ibfk_1 FOREIGN KEY (id_hotel) REFERENCES HOTEL(id_hotel)
  ); '''
execute_req(conn, sql_create_room)

In [38]:
sql_create_client = '''CREATE TABLE CLIENT(
    "id_client" TEXT PRIMARY KEY NOT NULL,
    country TEXT,
    nuitee INT,
    traveler_infos TEXT,
    review_title TEXT, 
    positive_review TEXT,
    negative_review TEXT, 
    usefulness_review TEXT,
    delay_comment INT
  ); '''
execute_req(conn, sql_create_client)


In [39]:
sql_create_date = '''CREATE TABLE DATE(
    id_date TEXT PRIMARY KEY NOT NULL,
    month_str TEXT,
    year INT,
    month_num INT,
    date DATE
  ); '''
execute_req(conn, sql_create_date)


In [40]:
sql_create_res = '''CREATE TABLE RESERVATION(
    id_reservation TEXT PRIMARY KEY NOT NULL,
    grade_review FLOAT,
    level_grade_review INT,
    id_room TEXT,
    id_date TEXT,
    id_client TEXT,
    CONSTRAINT RESERVATION_ibfk_1 FOREIGN KEY (id_room) REFERENCES ROOM(id_room),
    CONSTRAINT RESERVATION_ibfk_2 FOREIGN KEY (id_date) REFERENCES DATE(id_date),
    CONSTRAINT RESERVATION_ibfk_3 FOREIGN KEY (id_client) REFERENCES CLIENT(id_client)
  ); '''
execute_req(conn, sql_create_res)
    

# insert values

In [6]:
def insert_values(conn, df, table):
    tuples = [tuple(x) for x in df.to_numpy()]
    cols = ','.join(list(df.columns))
    # SQL query to execute
    query = "INSERT INTO %s(%s) VALUES %%s" % (table, cols)
    cursor = conn.cursor()
    try:
        extras.execute_values(cursor, query, tuples)
        conn.commit()
    except (Exception, psycopg2.DatabaseError) as error:
        print("Error: %s" % error)
        conn.rollback()
        cursor.close()
        return 1
    print("the dataframe is inserted")
    cursor.close()

In [42]:
insert_values(conn, date, 'date')

the dataframe is inserted


In [43]:
insert_values(conn, hotel, 'hotel')

the dataframe is inserted


In [44]:
insert_values(conn, room, 'room')

the dataframe is inserted


In [45]:
insert_values(conn, client, 'client')

the dataframe is inserted


In [46]:
insert_values(conn, reservation, 'reservation')

the dataframe is inserted


## get tables

In [4]:
try:
    conn = psycopg2.connect(
          user = "m139",
          password = "m139",
          host = "db-etu.univ-lyon2.fr",
          port = "5432",
          database = "m139"
    )
    cur = conn.cursor()
    reservation = "SELECT * FROM reservation"
    client = "SELECT * FROM client"
    hotel = "SELECT * FROM hotel"
    room = "SELECT * FROM room"
    date = "SELECT * FROM date"

    cur.execute(reservation)
    reservation = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])
    cur.execute(client)
    client = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])
    cur.execute(hotel)
    hotel = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])
    cur.execute(room)
    room = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])
    cur.execute(date)
    date = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])

    cur.close()
    conn.close()
except (Exception, psycopg2.Error) as error :
    print ("Erreur lors de la connexion à PostgreSQL", error)


hotel_room = hotel.merge(room, on="id_hotel")
res_client = reservation.merge(client, on="id_client")
res_client_date = res_client.merge(date, on="id_date")
df = res_client_date.merge(hotel_room, on="id_room")
df

id_reservation  grade_review  level_grade_review  \
0      2631f321-fd21-4956-9f0b-0a4bc0e5dae7           9.0                   2   
1      b09eac46-d540-4bc5-806a-a737c3606892           7.0                   1   
2      578ba80f-d734-4c9f-99b4-ba43776b78ca          10.0                   2   
3      04e84db4-103a-40c3-ba4b-736d188c09b2           9.0                   2   
4      31c7fea5-f246-4e2b-8f5a-5833f8a42b2f           8.0                   2   
...                                     ...           ...                 ...   
11214  23012349-f892-4a8d-9dab-9ca659c0a1e7           8.0                   2   
11215  f7ad1ebd-b9f5-4d05-948b-448d77751e5c           9.6                   2   
11216  2ee6251a-1b00-480a-9894-e1c018678b32          10.0                   2   
11217  9466fade-e8ef-428f-9609-cf16b054a697           8.0                   2   
11218  473468ff-0054-4174-a9a6-333f4f28f121           7.9                   1   

                                    id_room   id_date  \
0      3fd69528-3808-42db-8b85-5478b1092a14  20230101   
1      3fd69528-3808-42db-8b85-5478b1092a14  20230101   
2      3fd69528-3808-42db-8b85-5478b1092a14  20230101   
3      3fd69528-3808-42db-8b85-5478b1092a14  20230101   
4      3fd69528-3808-42db-8b85-5478b1092a14  20230101   
...                                     ...       ...   
11214  bee020b0-7a87-4430-bf70-b1499ff34967  20191201   
11215  f36d966b-8876-45d8-85eb-7de5ec7bceaf  20200101   
11216  f36d966b-8876-45d8-85eb-7de5ec7bceaf  20200301   
11217  2277a9aa-3602-472f-9414-6c19165d8094  20200301   
11218  e05b3ac3-5ee6-45a2-bbd2-e7bff8b413b7  20200301   

                                  id_client      country  nuitee  \
0      1de67bb1-041c-4738-8d78-2caa0b156d42  Royaume-Uni       1   
1      a211550b-d693-4eed-a030-f6a5ba6d1fbf     Belgique       1   
2      5ef62afa-cd01-4faa-9fd8-2c87e9e5ad24  Royaume-Uni       2   
3      71eb69c7-f1d1-47e3-88df-a90a4e255fda       France       1   
4      ef9d9c0f-c192-413e-837d-1a9c6b1d0301     Pays-Bas       1   
...                                     ...          ...     ...   
11214  f3b755e3-c3b5-4412-bf4d-5d6c80f3952b     Pays-Bas       1   
11215  0988541e-0aa0-496b-b5be-ac6a8af083c3   La Réunion       1   
11216  bffb4426-c483-408c-af68-7ade5b201e35       France       3   
11217  b2b7d146-4f09-41b9-b347-592809655253     Belgique       2   
11218  21456a19-8d95-4eb9-92ec-9141b44298df    Allemagne       3   

            traveler_infos                                       review_title  \
0                  Famille                            excellent and memorable   
1                  Famille                                              Bien    
2                  Famille                     amazing and very helpful staff   
3                  Famille                   On a passé un très bon moment !!   
4                  Famille  Fijn verblijf gehad, hebben nacht bijgeboekt e...   
...                    ...                                                ...   
11214               Groupe                                          Très bien   
11215              Famille                                       Exceptionnel   
11216              Famille                                       Exceptionnel   
11217  Voyageur individuel                                          Très bien   
11218              Famille                                              Bien    

       ... usefulness_review delay_comment month_str  year month_num  \
0      ...                 0             0   janvier  2023         1   
1      ...                 0             0   janvier  2023         1   
2      ...                 0             0   janvier  2023         1   
3      ...                 0             0   janvier  2023         1   
4      ...                 0             0   janvier  2023         1   
...    ...               ...           ...       ...   ...       ...   
11214  ...                 0             1  décembre  2019        12   
11215

In [2]:
try:
    conn = psycopg2.connect(
          user = "m140",
          password = "m140",
          host = "db-etu.univ-lyon2.fr",
          port = "5432",
          database = "m140"
    )
    cur = conn.cursor()
    history = "SELECT * FROM history"

    cur.execute(history)
    history = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])

    cur.close()
    conn.close()
except (Exception, psycopg2.Error) as error :
    print ("Erreur lors de la connexion à PostgreSQL", error)
    
len(history)

2262

In [8]:
os.chdir("C:/Users/pauli/Documents/M2/Text Mining/projet/Disney-Text-Mining/fichiers")
mypath = os.getcwd()

Scrapping_Sequoia_Lodge = pd.read_csv(str(mypath)+"/Scrapping_Sequoia_Lodge.csv",sep=';')
Scrapping_Santa_Fe = pd.read_csv(str(mypath)+"/Scrapping_Santa_Fe.csv",sep=';')
Scrapping_Newport_Bay_Club = pd.read_csv(str(mypath)+"/Scrapping_Newport_Bay_Club.csv",sep=';')
Scrapping_New_York = pd.read_csv(str(mypath)+"/Scrapping_New_York.csv",sep=';')
Scrapping_Davy_Crockett_Ranch = pd.read_csv(str(mypath)+"/Scrapping_Davy_Crockett_Ranch.csv",sep=';')

In [11]:
insert_values(conn, Scrapping_Sequoia_Lodge, 'history')

the dataframe is inserted


In [12]:
insert_values(conn, Scrapping_Santa_Fe, 'history')

the dataframe is inserted


In [13]:
insert_values(conn, Scrapping_Newport_Bay_Club, 'history')

the dataframe is inserted


In [14]:
insert_values(conn, Scrapping_New_York, 'history')

the dataframe is inserted


In [15]:
insert_values(conn, Scrapping_Davy_Crockett_Ranch, 'history')

the dataframe is inserted


In [27]:
try :
    conn = psycopg2.connect(
        user = "m140",
        password = "m140",
        host = "db-etu.univ-lyon2.fr",
        port = "5432",
        database = "m140"
    )

    cur = conn.cursor()

    history = "SELECT * FROM history"
    cur.execute(history)
    history = pd.DataFrame(cur.fetchall(), columns=[desc[0] for desc in cur.description])
    cur.close()
    conn.close()
except (Exception, psycopg2.Error) as error :
    print ("Erreur lors de la connexion à PostgreSQL", error)
print(len(history))

11327


In [29]:
import json
df = history.to_json()
df

'{"names":{"0":"Sarva","1":"Aurelie","2":"Chlo\\u00e9","3":"Hayley","4":"Emmanuelle","5":"Samantha","6":"Anonyme","7":"Giovanni","8":"Giovanni","9":"Davide","10":"Francois","11":"Joyce","12":"Emile","13":"Lingxue","14":"Lingxue","15":"Guy","16":"Tiffany","17":"Morgane","18":"Diane-sarah","19":"Anonyme","20":"Florine","21":"Andre","22":"Veronica","23":"Jessica","24":"Julie","25":"Anonyme","26":"Contant","27":"Nicaise","28":"Jo","29":"Cassandra","30":"Stephane","31":"M\\u00e9lissa","32":"Laurent","33":"Bel\\u00e9n","34":"Gretchen","35":"Catuxa","36":"Wayne","37":"Cl\\u00e9ment","38":"Sophie","39":"Fernandez","40":"Marquis","41":"Frank","42":"Meng","43":"Samanta","44":"Anonyme","45":"Pascal","46":"Kristian","47":"Paula","48":"Yasir","49":"Or","50":"Gizella","51":"Jasna","52":"Frederic","53":"Zo\\u00e9","54":"Amg77","55":"Karen","56":"St\\u00e9phane","57":"Matteo","58":"Etjan","59":"Sylvie","60":"Veronique","61":"Grazvella","62":"Kent","63":"Henry","64":"Simbaredo","65":"Rozaina","66":"Ann

In [24]:
history.dtypes


names                object
country              object
room_type            object
nuitee                int64
reservation_date     object
traveler_infos       object
date_review          object
review_title         object
grade_review         object
positive_review      object
negative_review      object
usefulness_review     int64
uniqueid             object
hotel                object
dtype: object